In [1]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Parkinsons_Disease"
cohort = "GSE30335"

# Input paths
in_trait_dir = "../../input/GEO/Parkinsons_Disease"
in_cohort_dir = "../../input/GEO/Parkinsons_Disease/GSE30335"

# Output paths
out_data_file = "../../output/preprocess/Parkinsons_Disease/GSE30335.csv"
out_gene_data_file = "../../output/preprocess/Parkinsons_Disease/gene_data/GSE30335.csv"
out_clinical_data_file = "../../output/preprocess/Parkinsons_Disease/clinical_data/GSE30335.csv"
json_path = "../../output/preprocess/Parkinsons_Disease/cohort_info.json"


### Step 1: Initial Data Loading

In [2]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


Background Information:
!Series_title	"Genomic Signatures for Pesticide Exposure in Latino Farmworkers"
!Series_summary	"We tested the hypothesis that differential  gene expression in whole blood will reveal candidate blood biomarkers for exposure to agricultural pesticides and herbicides.  Blood gene expression in male Latino farmworkers, where chronic pesticide exposure is occupational, was compared to blood gene expression in age and gender matched Latino manual workers. We identified an expression signature for farmwork, differential expression in genes that correlated with levels of urinary pesticide metabolites, alterations in axonal guidance pathways and statistical models that link farmworker differential expression to Parkinson's disease."
!Series_overall_design	"Case control, 20 male Latino farmworkers compared to 20 age matched male Latino manual workers. "
Sample Characteristics Dictionary:
{0: ['occupation: Manual Worker', 'occupation: Farmworker'], 1: ['worker id: W001', 

### Step 2: Dataset Analysis and Clinical Feature Extraction

In [3]:
# Analysis and answers to questions
# 1. Gene Expression Data Availability
# From the background information, this study compares blood gene expression between Latino farmworkers
# and manual workers, indicating gene expression data is available.
is_gene_available = True

# 2. Variable Availability and Data Type Conversion
# 2.1 Data Availability

# For trait (Parkinson's Disease):
# From background, farmworkers have increased exposure to pesticides which is linked to Parkinson's disease
# We can use 'occupation' as a proxy for exposure risk for Parkinson's
trait_row = 0  # The occupation field (farmworker vs manual worker)

# For age:
# There's no explicit age information in the sample characteristics dictionary
age_row = None

# For gender:
# The background states all participants are male, so gender is constant
gender_row = None

# 2.2 Data Type Conversion Functions

def convert_trait(value):
    """Convert occupation to binary trait (exposure risk for Parkinson's)"""
    if not isinstance(value, str):
        return None
    
    value = value.lower().split(": ")[-1].strip()
    
    if "farmworker" in value:
        return 1  # Higher pesticide exposure (risk factor for Parkinson's)
    elif "manual worker" in value:
        return 0  # Lower pesticide exposure 
    else:
        return None

def convert_age(value):
    """Convert age to continuous value - Not applicable for this dataset"""
    return None

def convert_gender(value):
    """Convert gender to binary - Not applicable for this dataset"""
    return None

# 3. Save Metadata
# Trait data is available (trait_row is not None)
is_trait_available = trait_row is not None
validate_and_save_cohort_info(
    is_final=False,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available
)

# 4. Clinical Feature Extraction
if trait_row is not None:
    # Extract clinical features from the clinical data DataFrame
    clinical_features = geo_select_clinical_features(
        clinical_df=clinical_data,
        trait=trait,
        trait_row=trait_row,
        convert_trait=convert_trait,
        age_row=age_row,
        convert_age=convert_age,
        gender_row=gender_row,
        convert_gender=convert_gender
    )
    
    # Preview the extracted clinical features
    print("Preview of clinical features:")
    print(preview_df(clinical_features))
    
    # Save to CSV
    clinical_features.to_csv(out_clinical_data_file)
    print(f"Clinical data saved to {out_clinical_data_file}")


Preview of clinical features:
{'GSM752043': [0.0], 'GSM752044': [0.0], 'GSM752045': [0.0], 'GSM752046': [0.0], 'GSM752047': [0.0], 'GSM752049': [0.0], 'GSM752050': [0.0], 'GSM752051': [0.0], 'GSM752052': [0.0], 'GSM752053': [0.0], 'GSM752054': [0.0], 'GSM752055': [0.0], 'GSM752056': [0.0], 'GSM752057': [0.0], 'GSM752058': [0.0], 'GSM752059': [0.0], 'GSM752060': [0.0], 'GSM752061': [0.0], 'GSM752062': [0.0], 'GSM752064': [0.0], 'GSM752065': [1.0], 'GSM752066': [1.0], 'GSM752068': [1.0], 'GSM752069': [1.0], 'GSM752070': [1.0], 'GSM752071': [1.0], 'GSM752072': [1.0], 'GSM752073': [1.0], 'GSM752075': [1.0], 'GSM752076': [1.0], 'GSM752077': [1.0], 'GSM752078': [1.0], 'GSM752080': [1.0], 'GSM752081': [1.0], 'GSM752082': [1.0], 'GSM752084': [1.0], 'GSM752085': [1.0], 'GSM752086': [1.0], 'GSM752087': [1.0], 'GSM752088': [1.0]}
Clinical data saved to ../../output/preprocess/Parkinsons_Disease/clinical_data/GSE30335.csv


### Step 3: Gene Data Extraction

In [4]:
# 1. First get the file paths again to access the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Use the get_genetic_data function from the library to get the gene_data from the matrix_file
gene_data = get_genetic_data(matrix_file)

# 3. Print the first 20 row IDs (gene or probe identifiers) for future observation
print("First 20 gene/probe identifiers:")
print(gene_data.index[:20])


First 20 gene/probe identifiers:
Index(['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at', '1294_at',
       '1316_at', '1320_at', '1405_i_at', '1431_at', '1438_at', '1487_at',
       '1494_f_at', '1552256_a_at', '1552257_a_at', '1552258_at', '1552261_at',
       '1552263_at', '1552264_a_at', '1552266_at'],
      dtype='object', name='ID')


### Step 4: Gene Identifier Review

In [5]:
# These identifiers are not human gene symbols but rather Affymetrix probe IDs.
# Affymetrix probe IDs typically have formats like "1007_s_at", "1053_at", etc.
# They need to be mapped to official gene symbols for more interpretable analysis.

requires_gene_mapping = True


### Step 5: Gene Annotation

In [6]:
# 1. First get the file paths using geo_get_relevant_filepaths function
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Use the 'get_gene_annotation' function from the library to get gene annotation data from the SOFT file.
gene_annotation = get_gene_annotation(soft_file)

# 3. Use the 'preview_df' function from the library to preview the data and print out the results.
print("Gene annotation preview:")
print(preview_df(gene_annotation))


Gene annotation preview:
{'ID': ['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at'], 'GB_ACC': ['U48705', 'M87338', 'X51757', 'X69699', 'L36861'], 'SPOT_ID': [nan, nan, nan, nan, nan], 'Species Scientific Name': ['Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens'], 'Annotation Date': ['Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014'], 'Sequence Type': ['Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence'], 'Sequence Source': ['Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database'], 'Target Description': ['U48705 /FEATURE=mRNA /DEFINITION=HSU48705 Human receptor tyrosine kinase DDR gene, complete cds', 'M87338 /FEATURE= /DEFINITION=HUMA1SBU Human replication factor C, 40-kDa subunit (A1) mRNA, complete cds', "X51757 /FEATURE=cds /DEFINITION=HSP70B Human heat-shock protein HSP70B' gene", 'X69699 /FEATURE= /DEF

### Step 6: Gene Identifier Mapping

In [7]:
# 1. Observe gene annotation data to determine identifiers and gene symbols
# Based on the preview, the identifier in gene_data is in the 'ID' column
# The gene symbols are in the 'Gene Symbol' column

# 2. Get gene mapping dataframe
gene_mapping = get_gene_mapping(gene_annotation, 'ID', 'Gene Symbol')

# 3. Apply gene mapping to convert from probe-level measurements to gene expression
gene_data = apply_gene_mapping(gene_data, gene_mapping)

# Print some information about the resulting gene expression data
print(f"Converted expression data from probes to genes")
print(f"Number of genes: {len(gene_data)}")
print("First 10 gene symbols:")
print(gene_data.index[:10])


Converted expression data from probes to genes
Number of genes: 21278
First 10 gene symbols:
Index(['A1BG', 'A1BG-AS1', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1', 'A2MP1',
       'A4GALT', 'A4GNT', 'AA06'],
      dtype='object', name='Gene')


### Step 7: Data Normalization and Linking

In [8]:
# 1. Normalize gene symbols from the already mapped gene expression data from Step 6
# Apply normalization to standardize gene symbols
normalized_gene_data = normalize_gene_symbols_in_index(gene_data)
print(f"Gene expression data shape after normalization: {normalized_gene_data.shape}")
print("First 5 normalized gene symbols:")
print(normalized_gene_data.index[:5])

# Save the normalized gene data
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
normalized_gene_data.to_csv(out_gene_data_file)
print(f"Normalized gene data saved to {out_gene_data_file}")

# 2. Load the clinical data that was already processed in Step 2
# We need to load the clinical data from the file that was saved in Step 2
if os.path.exists(out_clinical_data_file):
    clinical_data_processed = pd.read_csv(out_clinical_data_file, index_col=0)
    print("Loaded clinical data from file")
else:
    # If for some reason the file wasn't saved, recreate the clinical features using the same parameters as in Step 2
    soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)
    background_info, clinical_data = get_background_and_clinical_data(matrix_file)
    
    # Use the same conversion function and trait_row from Step 2
    def convert_trait(value):
        """Convert occupation to binary trait (exposure risk for Parkinson's)"""
        if not isinstance(value, str):
            return None
        
        value = value.lower().split(": ")[-1].strip()
        
        if "farmworker" in value:
            return 1  # Higher pesticide exposure (risk factor for Parkinson's)
        elif "manual worker" in value:
            return 0  # Lower pesticide exposure 
        else:
            return None
    
    # Use the exact same parameters as we determined in Step 2
    clinical_data_processed = geo_select_clinical_features(
        clinical_df=clinical_data,
        trait=trait,
        trait_row=0,  # From Step 2
        convert_trait=convert_trait,
        age_row=None,  # From Step 2
        convert_age=None,
        gender_row=None,  # From Step 2
        convert_gender=None
    )
    
    # Save it again just to be sure
    os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
    clinical_data_processed.to_csv(out_clinical_data_file)

print("Clinical data shape:", clinical_data_processed.shape)
print("Clinical data preview:")
print(preview_df(clinical_data_processed))

# 3. Link clinical and genetic data
# The clinical data is oriented with genes/traits as rows and samples as columns
# Transpose the normalized gene data to match this orientation (samples as columns)
genetic_data_t = normalized_gene_data

# Link clinical and genetic data vertically
linked_data = geo_link_clinical_genetic_data(clinical_data_processed, genetic_data_t)
print(f"Linked data shape: {linked_data.shape}")

# 4. Handle missing values
linked_data = handle_missing_values(linked_data, trait)
print(f"Data shape after handling missing values: {linked_data.shape}")

# 5. Determine if trait and demographic features are biased
is_biased, linked_data = judge_and_remove_biased_features(linked_data, trait)
print(f"Data shape after removing biased features: {linked_data.shape}")
print(f"Is the trait biased: {is_biased}")

# 6. Validate and save cohort info
is_usable = validate_and_save_cohort_info(
    is_final=True,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=True,
    is_trait_available=True,
    is_biased=is_biased,
    df=linked_data,
    note="Dataset contains gene expression data from blood samples comparing farmworkers (with higher pesticide exposure, a risk factor for Parkinson's) to manual workers."
)

# 7. Save linked data if usable
if is_usable:
    os.makedirs(os.path.dirname(out_data_file), exist_ok=True)
    linked_data.to_csv(out_data_file)
    print(f"Linked data saved to {out_data_file}")
else:
    print("Dataset deemed not usable. Linked data was not saved.")

Gene expression data shape after normalization: (19845, 40)
First 5 normalized gene symbols:
Index(['A1BG', 'A1BG-AS1', 'A1CF', 'A2M', 'A2M-AS1'], dtype='object', name='Gene')


Normalized gene data saved to ../../output/preprocess/Parkinsons_Disease/gene_data/GSE30335.csv
Loaded clinical data from file
Clinical data shape: (1, 40)
Clinical data preview:
{'GSM752043': [0.0], 'GSM752044': [0.0], 'GSM752045': [0.0], 'GSM752046': [0.0], 'GSM752047': [0.0], 'GSM752049': [0.0], 'GSM752050': [0.0], 'GSM752051': [0.0], 'GSM752052': [0.0], 'GSM752053': [0.0], 'GSM752054': [0.0], 'GSM752055': [0.0], 'GSM752056': [0.0], 'GSM752057': [0.0], 'GSM752058': [0.0], 'GSM752059': [0.0], 'GSM752060': [0.0], 'GSM752061': [0.0], 'GSM752062': [0.0], 'GSM752064': [0.0], 'GSM752065': [1.0], 'GSM752066': [1.0], 'GSM752068': [1.0], 'GSM752069': [1.0], 'GSM752070': [1.0], 'GSM752071': [1.0], 'GSM752072': [1.0], 'GSM752073': [1.0], 'GSM752075': [1.0], 'GSM752076': [1.0], 'GSM752077': [1.0], 'GSM752078': [1.0], 'GSM752080': [1.0], 'GSM752081': [1.0], 'GSM752082': [1.0], 'GSM752084': [1.0], 'GSM752085': [1.0], 'GSM752086': [1.0], 'GSM752087': [1.0], 'GSM752088': [1.0]}
Linked data shape: (

Data shape after handling missing values: (40, 19846)
For the feature 'Parkinsons_Disease', the least common label is '0.0' with 20 occurrences. This represents 50.00% of the dataset.
The distribution of the feature 'Parkinsons_Disease' in this dataset is fine.

Data shape after removing biased features: (40, 19846)
Is the trait biased: False


Linked data saved to ../../output/preprocess/Parkinsons_Disease/GSE30335.csv
